In [1]:
import pandas as pd
import numpy as np
import csv
import nltk
from nltk.stem import PorterStemmer
from nltk.tokenize import WordPunctTokenizer
from __future__ import division
import matplotlib
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.feature_extraction.text import TfidfTransformer

In [2]:
nltk.download("stopwords")
from nltk.corpus import stopwords
esw = stopwords.words("english")
from string import punctuation

#remove "num", because "num" has the highest term frequency(45538) at the orinal file, 
#the second most frequent term only has a freq. of 3750
esw = esw + ['abstract', 'ci', 'hr','l','pubmed', 'num'] 

[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\D070678\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


In [3]:
from collections import defaultdict
from gensim import corpora

C:\Users\D070678\AppData\Local\Continuum\anaconda3\lib\site-packages\gensim\utils.py:1197: UserWarning: detected Windows; aliasing chunkize to chunkize_serial
  warnings.warn("detected Windows; aliasing chunkize to chunkize_serial")


In [4]:
import datetime

In [27]:
####read file

#read train.docs file
train_doc_file = pd.read_csv("train.docs", encoding = 'utf-8', sep='\t', header=None)
train_doc_file.columns = ['id', 'text']

#read train.nontopic-titles.queries file
train_query_file = pd.read_csv("train.nontopic-titles.queries", encoding = 'utf-8', sep='\t', header=None)
train_query_file.columns = ['id', 'text']



### preprocessing

train_doc_file["text"] = train_doc_file['text'].str.replace('/', ' or ')

train_doc_file["text"] = train_doc_file['text'].str.replace('-', ' and ')

train_query_file["text"] = train_query_file['text'].str.replace('/', ' or ')

train_query_file["text"] = train_query_file['text'].str.replace('-', ' and ')

def removeStopwords(file):
    i = 0
    for el in file:
        el = ' '.join([word for word in el.lower().split() if word not in esw])
        file[i] = el
        i += 1
def removePunctuation(file):
    i = 0
    for el in file:
        el = ' '.join([word for word in el.lower().split() if word not in punctuation])
        file[i] = el
        i += 1

def stemming(file):
    ps = PorterStemmer()
    i = 0
    for el in file:
        el = ' '.join([ps.stem(word) for word in el.lower().split() ])
        file[i] = el
        i += 1
        
    

In [28]:
### remove stopwords


removeStopwords(train_doc_file['text'])
removeStopwords(train_query_file['text'])

#stemming(train_doc_file['text'])
#stemming(train_query_file['text'])




### remove punctuation
removePunctuation(train_doc_file['text'])
removePunctuation(train_query_file['text'])

In [9]:
######### Don't Run ############################

#texts = [[word for word in document.split()] for document in train_doc_file['text']]

#frequency = defaultdict(int)


#for text in texts:
     #for token in text:
        #frequency[token] += 1

#texts = [[token for token in text if frequency[token] > 0]
          #for text in texts]

#dictionary = corpora.Dictionary(texts)
#corpus = [dictionary.doc2bow(text) for text in texts]

In [85]:
######### Don't Run ############################
#vocabulary = list()
#texts_query = [[word for word in document.split()] for document in train_query_file['text']]
#for text in texts_query:
    #for word in text:
        #vocabulary.append(word)
#vocabulary = list(set(vocabulary))
#vocabulary

['chives',
 'ligands',
 'calisthenic',
 'lipopolysaccharide-induced',
 'forest',
 'gonadal',
 'ast',
 'reduction',
 'toddlers',
 'polyunsaturated',
 'bdg',
 'bigelow',
 'capsule',
 'robust',
 'complaints',
 'peracetic',
 'cerebrospinal',
 'underestimated',
 'register',
 'sinensis',
 'collagen',
 'electrolyte',
 'public',
 'intakes',
 'anxiety',
 'wider',
 'pens',
 'deterioration',
 'isrctn',
 'homa-ir',
 'potentially',
 'hemicolectomy',
 'nongastrointestinal',
 'tasted',
 'l-cpt',
 'anomalies',
 'gain',
 'collapsed',
 'formula-fed',
 'surplus',
 'cesarean',
 'pro-raw',
 'portfolio',
 'extractable',
 'pathophysiological',
 'exploration',
 'regression',
 'gallus',
 'increasing',
 'fundamental',
 'radio-fe',
 'interested',
 'univariate',
 'counties',
 'elusive',
 'severely',
 'concentrates',
 'integrative',
 'beneath',
 'pharmacokinetics',
 'method--that',
 'brominated',
 'equivalents',
 'dosed',
 'process',
 'cost-effectively',
 'strawberry',
 'nocturnal',
 'thirty',
 'phoning',
 'polyom

In [7]:
# run this before function getTieredIndex(doc_File, query_File)
#get the term frequency for specific term in a list

def getTermFrequency(word, wordList):
    
    if word in wordList:
        frequency = defaultdict(int)
        for el in wordList:
            frequency[el]+=1

        return frequency[word]  
    else:
        print("Error:", word, "is not in the wordList")
        
        
    

In [8]:
#@ run this before function getTieredIndex(doc_File, query_File)

# sort the docs in for each word by term frequency
# return a sorted tiers dictionary for each token in query file


def sortingDocByTF(vocabulary, docs_clustering ):
    
    sorted_one_level_tier = defaultdict(list)
    for token in vocabulary:
        m = docs_clustering[token]
        l = []
        r = []
        for i in range(len(m)):
            l.append(m[i][0])
            r.append(m[i][1])

        new_list = []
        while m:  
            # find index of maximum item
            max_index = r.index(max(r)) 

            # remove item with pop() and append to sorted list
            r.pop(max_index)
            new_list.append(m.pop(max_index))

        sorted_one_level_tier[token] = new_list
    return sorted_one_level_tier

In [9]:
# retrun: a defaultdict, it stores for each term, the docID of docs that contain the word
# doc_File: the orgional imported doc file
# query_File: the origional imported query file

def getTieredIndex(doc_File, query_File):
    
    documents_doc = doc_File['text']
    documents_id = list(doc_File['id'])
    documents_query = query_File['text']
    
    
    if type(documents_query) is str:
        print("Error: the input query_File should be an interate file") 
        
    else: 
        ##################### create doc tiers for each term in each query ###############################
        
        texts_doc = [[word for word in document.split()] for document in documents_doc] 
        texts_query = [[word for word in document.split()] for document in documents_query]

        vocabulary = list()
        for text in texts_query:
            for word in text:
                vocabulary.append(word)
        vocabulary = list(set(vocabulary)) #get vocabulary list of query file        
        
        frequency = defaultdict(int) #initiate dictionary

        for text in texts_query:
             for token in text:
                frequency[token] += 1

        tokens_query = [[token for token in text if frequency[token] > 0]
              for text in texts_query]

        docs_clustering = defaultdict(list)

        ### for each term in vocabulary, get all of the (doc, tf) pairs, docs are docs that contain the term 
        for word in vocabulary:
            for i in range(len(texts_doc)):
                if word in texts_doc[i]:
                    docs_clustering[word].append([documents_id[i], getTermFrequency(word, texts_doc[i])]) 
    
        sorted_one_level_tier = sortingDocByTF(vocabulary, docs_clustering )
    
        return sorted_one_level_tier        


In [10]:
### test for the function getTieredIndex(doc_File, query_File)
# without being stemmed
doc_Tiers = getTieredIndex(train_doc_file, train_query_file)
doc_Tiers

defaultdict(list,
            {'sticky': [],
             'sore': [['MED-957', 1],
              ['MED-1129', 1],
              ['MED-2271', 1],
              ['MED-4839', 1]],
             'kiwi': [['MED-1695', 6], ['MED-4325', 1]],
             'blue': [['MED-1268', 4],
              ['MED-2616', 3],
              ['MED-1376', 2],
              ['MED-2979', 2],
              ['MED-3351', 2],
              ['MED-2172', 1],
              ['MED-2618', 1],
              ['MED-2888', 1],
              ['MED-2889', 1],
              ['MED-2899', 1],
              ['MED-3354', 1],
              ['MED-4385', 1],
              ['MED-4869', 1],
              ['MED-4938', 1],
              ['MED-5025', 1],
              ['MED-5131', 1],
              ['MED-5172', 1],
              ['MED-5173', 1]],
             'circulation': [['MED-1637', 2],
              ['MED-1748', 2],
              ['MED-967', 1],
              ['MED-2107', 1],
              ['MED-2110', 1],
              ['MED-2304', 1],

In [21]:
######### Don't Run ############################
### test for the function getTieredIndex(doc_File, query_File)
#stemmed

doc_Tiers_stemmed = getTieredIndex(train_doc_file, train_query_file)
doc_Tiers_stemmed

defaultdict(list,
            {'remedi': [['MED-3750', 4],
              ['MED-2441', 2],
              ['MED-557', 1],
              ['MED-719', 1],
              ['MED-724', 1],
              ['MED-912', 1],
              ['MED-1009', 1],
              ['MED-1444', 1],
              ['MED-1919', 1],
              ['MED-2021', 1],
              ['MED-2144', 1],
              ['MED-2707', 1],
              ['MED-2817', 1],
              ['MED-2818', 1],
              ['MED-2821', 1],
              ['MED-2921', 1],
              ['MED-3019', 1],
              ['MED-3758', 1],
              ['MED-3807', 1],
              ['MED-4365', 1],
              ['MED-4374', 1],
              ['MED-4712', 1],
              ['MED-4856', 1],
              ['MED-5121', 1],
              ['MED-5163', 1],
              ['MED-5216', 1],
              ['MED-5283', 1]],
             'putrefi': [],
             'fatti': [['MED-1454', 15],
              ['MED-4626', 11],
              ['MED-4551', 8],
      

In [11]:
### create DTM

 ## get DTM, weighted by tfidf
def get_DTM_tfidf(file):
    train_count_vect = CountVectorizer() #remove english stopwords
    X_train_counts = train_count_vect.fit_transform(file)
    vocabulary = list(train_count_vect.vocabulary_.keys())
    

    tfidf_transformer = TfidfTransformer()
    X_train_tfidf = tfidf_transformer.fit_transform(X_train_counts)
    return X_train_tfidf


## get DTM, weighted by tfidf
def get_DTM_tf(file):
    train_count_vect = CountVectorizer() #remove english stopwords
    X_train_counts = train_count_vect.fit_transform(file)

    tf_transformer = TfidfTransformer(use_idf=False).fit(X_train_counts)
    X_train_tf = tf_transformer.transform(X_train_counts)
    return X_train_tf

In [12]:
### create tfidf weighted DTM for the train.docs file
train_tfidf = get_DTM_tfidf(train_doc_file.text)
train_tfidf

<3612x23449 sparse matrix of type '<class 'numpy.float64'>'
	with 310355 stored elements in Compressed Sparse Row format>

In [22]:
### create tfidf weighted DTM for the train.docs file
train_tfidf_stemmed = get_DTM_tfidf(train_doc_file.text)
train_tfidf_stemmed

<3612x16322 sparse matrix of type '<class 'numpy.float64'>'
	with 289370 stored elements in Compressed Sparse Row format>

In [14]:
###Generate the query vector
def get_QueryVector(queryFile, docFile):
    train_count_vect = CountVectorizer() #remove english stopwords
    X_train_counts = train_count_vect.fit_transform(docFile)
    vocabulary = list(train_count_vect.vocabulary_.keys())
    
    
    if type(queryFile) is str:
        query_vect = []
        query = queryFile
        query = query.split()
        frequency = defaultdict(int)
        for el in vocabulary:
            if el in query:
                frequency[el]+= 1
            else:
                frequency[el] = 0
        query_vect = list(dict(frequency).values() )   
    else:
        query_vect = CountVectorizer(analyzer = "word", vocabulary = vocabulary)
        query_vect = query_vect.fit_transform(queryFile)
    return query_vect

In [15]:
### create query vector matrix for the train.nontopic-titles.queries file 
query_vect = get_QueryVector(train_query_file.text, train_doc_file.text)
query_vect

<1141x23449 sparse matrix of type '<class 'numpy.int64'>'
	with 4192 stored elements in Compressed Sparse Row format>

In [23]:
### create query vector matrix for the train.nontopic-titles.queries file 
query_vect_stemmed = get_QueryVector(train_query_file.text, train_doc_file.text)
query_vect_stemmed

<1141x16322 sparse matrix of type '<class 'numpy.int64'>'
	with 4293 stored elements in Compressed Sparse Row format>

In [85]:
#def intersect(d):
    #if len(d)> 0:
        #result = d[0]
        #for el in d:
            #result = set(result).intersection(el)
    #return min(d)
        
                

In [76]:
######### Don't Run ############################

# return the minium intersection of tieres list
# input d: is a list of tieres, each tier is the index list of doc which contains a term of a query

def intersect(d):
    if len(d)> 0:
        resultsList = list()
        result = d[0]
        for el in d:
            if len(result) >=10 :
                r = result
                result = set(result).intersection(el)
                if len(result)==0:
                    return r
                    break
                
                
        

In [16]:
#@ run this before function IRByTieredIndex(query_File, doc_Tiers, query_vect, DTM_tfidf, doc_File ):

# return the minium intersection of tieres list
# input d: is a list of tieres, each tier is the index list of doc which contains a term of a query

def intersect(d):
    resultsList = list()
    l= []
    if len(d)> 0:
        
        result = d[0]
        for el in d:
            
            if len(result) >0:
                resultsList.append(result)
                result = set(result).intersection(el)
            else:
                result = resultsList[len(resultsList)-1]
        #print(resultsList)
        if len(resultsList) >0:
            for el in resultsList:
                l.append(len(el))
            #print(resultsList[np.argmin(l)])
            return(resultsList[np.argmin(l)])
    else:
        for el in d:
            l.append(len(el))    
        return(d[np.argmin(l)])
        
            

In [24]:
### retrieve through tiered index model
# get the doc and similarity for each query

# doc_File: the orgional imported doc file
# query_File: the origional imported query file
# doc_Tiers: output of the function getTieredIndex(doc_File, query_File)
# query_vect: tf weighted query-term matrix
# DTM_tfidf: tfidf weighted DTM
    

def IRByTieredIndex(query_File, doc_Tiers, query_vect, DTM_tfidf, doc_File ):
    
    documents_id = list(doc_File['id'])
    query_id = list(query_File['id'])
    
    query_file = query_File['text']
    doc_tiers = doc_Tiers
    
    if type(query_file) is str:
        print("Error: the input query_File should be an interate text file") 
        
    else: 
        r =[]
        
        texts_query = [[word for word in q.split()] for q in query_file]
        
        # get vocabulary list for each query 
        for i in range(len(texts_query)):
            texts_query[i] = list(set(texts_query[i]))
        
        
        for i in range(len(texts_query)):
            
            docs_all = [] 
            for word in texts_query[i]:
                tieres = []
                for d in doc_Tiers[word]:
                    tieres.append(d[0])
                if len(tieres)>0:
                    docs_all.append(tieres)
            #print(len(docs_all))
            #print(docs_all)
            if len(docs_all) >0:

                results = list(intersect(docs_all))

                #print(results)

                if len(results) >0:

                    sims = []
                    sims_docs = []
                    for el in results:
                        query_vector = query_vect[i]
                        doc_vector = DTM_tfidf[documents_id.index(el)]
                        sims.append(np.dot(query_vector, doc_vector.transpose())[0,0])
                        sims_docs.append(documents_id.index(el))

                    for x in range(len(sims)):
                        if sims[x] >0:
                            
                            r.append([str(query_id[i]), str(documents_id[sims_docs[x]]), sims[x]])
                            #print(str(query_id[i]), 0 ,str(documents_id[sims_docs[x]]), sims[x])
                            
        return r

                            



            #return results    


In [29]:
####################IRByTieredIndex result1, need to get the performance result #########################

# without being stemmed, "-" converted to "and"

# test the IR on the whole query file
t1 =  datetime.datetime.now()
IR_results = IRByTieredIndex(train_query_file, doc_Tiers, query_vect, train_tfidf, train_doc_file )
t2 =  datetime.datetime.now()
t = t2-t1

print("running time:", t )
# save result
df = pd.DataFrame(IR_results, columns = ['QUERY_ID', 'DOC_ID', 'sim_results'])

df.to_csv('IRByTieredIndex result1.csv', header=None, index=None, sep=' ', mode='a')
df


running time: 0:00:36.122157


QUERY_ID    DOC_ID  sim_results
0     PLAIN-10  MED-1603     0.047786
1    PLAIN-116  MED-1060     0.054898
2    PLAIN-116  MED-2263     0.052490
3    PLAIN-117  MED-2664     0.052117
4    PLAIN-117  MED-1182     0.033349
5    PLAIN-117   MED-859     0.153104
6    PLAIN-118  MED-1060     0.054898
7    PLAIN-118  MED-2263     0.052490
8    PLAIN-128  MED-2809     0.068976
9    PLAIN-130  MED-5231     0.171365
10   PLAIN-130  MED-2249     0.026285
11   PLAIN-130  MED-4691     0.034690
12   PLAIN-155  MED-3673     0.037576
13   PLAIN-163  MED-2527     0.027212
14   PLAIN-163  MED-2750     0.073514
15   PLAIN-166  MED-2905     0.041756
16   PLAIN-166  MED-3032     0.041756
17   PLAIN-166  MED-1153     0.058898
18   PLAIN-170  MED-4850     0.051602
19   PLAIN-173  MED-3020     0.023498
20   PLAIN-173  MED-4621     0.033464
21   PLAIN-173   MED-709     0.142155
22   PLAIN-173  MED-1314     0.040011
23   PLAIN-173  MED-2264     0.080437
24   PLAIN-181  MED-3781     0.084438
25   PLAIN-192  MED-4752     0.098495
26   PLAIN-192  MED-1595     0.074208
27   PLAIN-192  MED-4753     0.111911
28   PLAIN-215  MED-5166     0.093672
29   PLAIN-215  MED-3484     0.320562
..         ...       ...          ...
342  PLAIN-361  MED-3485     0.085772
343  PLAIN-361  MED-3502     0.022922
344  PLAIN-361  MED-4200     0.042358
345  PLAIN-361  MED-4203     0.043341
346  PLAIN-361  MED-4295     0.042684
347  PLAIN-361  MED-4393     0.085772
348  PLAIN-361  MED-4469     0.046071
349  PLAIN-361  MED-4551     0.152960
350  PLAIN-361  MED-4627     0.102549
351  PLAIN-361  MED-4691     0.034690
352  PLAIN-361  MED-4702     0.080850
353  PLAIN-361  MED-4771     0.265182
354  PLAIN-361  MED-4863     0.141766
355  PLAIN-361  MED-5269     0.031905
356  PLAIN-386  MED-3744     0.077849
357  PLAIN-392  MED-3282     0.044972
358  PLAIN-392  MED-4055     0.090401
359  PLAIN-402  MED-3255     0.032189
360  PLAIN-402  MED-3959     0.021233
361  PLAIN-402  MED-2656     0.103419
362  PLAIN-402  MED-2479     0.023733
363  PLAIN-416  MED-4298     0.075351
364  PLAIN-423  MED-3673     0.037576
365  PLAIN-427  MED-3818     0.052044
366  PLAIN-455  MED-1718     0.080972
367   PLAIN-49  MED-1028     0.014691
368   PLAIN-63   MED-876     0.145316
369   PLAIN-74  MED-4612     0.027307
370    PLAIN-9  MED-5101     0.287841
371   PLAIN-95  MED-2040     0.045072

[372 rows x 3 columns]

In [26]:
####################IRByTieredIndex result2, need to get the performance result #########################

# stemmed, "-" converted to "and"

# test the IR on the whole query file
t1 =  datetime.datetime.now()
IR_results = IRByTieredIndex(train_query_file, doc_Tiers_stemmed, query_vect_stemmed, train_tfidf_stemmed, train_doc_file )
t2 =  datetime.datetime.now()
t = t2-t1

print("running time:", t )
# save result
df = pd.DataFrame(IR_results, columns = ['QUERY_ID', 'DOC_ID', 'sim_results'])
df.to_csv('IRByTieredIndex result2.csv', header=None, index=None, sep=' ', mode='a')
df


running time: 0:00:31.874614


QUERY_ID    DOC_ID  sim_results
0     PLAIN-10  MED-1140     0.114206
1     PLAIN-10  MED-4932     0.070334
2    PLAIN-106  MED-2788     0.140474
3    PLAIN-108  MED-1169     0.040649
4    PLAIN-108  MED-1178     0.035217
5    PLAIN-108  MED-1182     0.034270
6    PLAIN-116  MED-3424     0.059322
7    PLAIN-148  MED-4136     0.081663
8    PLAIN-148  MED-2749     0.062918
9    PLAIN-149  MED-5033     0.081022
10   PLAIN-149  MED-2574     0.043441
11   PLAIN-149  MED-3799     0.053518
12   PLAIN-149  MED-4502     0.115811
13   PLAIN-149  MED-2585     0.043514
14   PLAIN-149  MED-4234     0.167353
15   PLAIN-149  MED-1028     0.010066
16   PLAIN-149  MED-1701     0.065076
17   PLAIN-149  MED-2300     0.151327
18   PLAIN-149  MED-4324     0.046399
19   PLAIN-149  MED-1512     0.132693
20   PLAIN-149  MED-4559     0.047092
21   PLAIN-156  MED-3172     0.119887
22   PLAIN-158  MED-3716     0.079847
23    PLAIN-17  MED-3730     0.068082
24   PLAIN-178  MED-3697     0.117067
25   PLAIN-198  MED-3427     0.069056
26   PLAIN-198  MED-2304     0.106285
27   PLAIN-198  MED-1355     0.088444
28   PLAIN-198  MED-1055     0.058127
29   PLAIN-198  MED-5299     0.110624
..         ...       ...          ...
561  PLAIN-361  MED-2325     0.062646
562  PLAIN-361  MED-2383     0.084982
563  PLAIN-361  MED-2650     0.043668
564  PLAIN-361  MED-2895     0.074489
565  PLAIN-361  MED-2986     0.033949
566  PLAIN-361  MED-3494     0.235103
567  PLAIN-361  MED-3896     0.087545
568  PLAIN-361  MED-3900     0.087967
569  PLAIN-361  MED-3925     0.047804
570  PLAIN-361  MED-4250     0.046913
571  PLAIN-361  MED-4484     0.179377
572  PLAIN-361  MED-4747     0.028643
573  PLAIN-361  MED-5074     0.056160
574  PLAIN-361  MED-5290     0.034406
575  PLAIN-372  MED-1682     0.101926
576  PLAIN-373  MED-1790     0.201824
577  PLAIN-373  MED-1674     0.047334
578  PLAIN-373  MED-1991     0.071213
579  PLAIN-373  MED-4036     0.044026
580  PLAIN-373  MED-4156     0.061171
581  PLAIN-373  MED-5007     0.051035
582   PLAIN-38   MED-557     0.085746
583  PLAIN-435  MED-5160     0.066415
584   PLAIN-49  MED-2284     0.095052
585   PLAIN-52  MED-5105     0.046869
586   PLAIN-53  MED-3086     0.059723
587   PLAIN-53  MED-2617     0.044902
588   PLAIN-53  MED-1574     0.030578
589   PLAIN-94  MED-4983     0.073251
590   PLAIN-94  MED-1606     0.070235

[591 rows x 3 columns]